In [35]:
import polars as pl
import geopandas as gpd
from pathlib import Path
import folium
import pandas as pd

# Data Load

First, we read in the shapefile for the gridcell covariates.

In [2]:
gdf = gpd.read_file("./data/raw/NABat_grid_covariates/NABat_grid_covariates.shp")


Now we read in all the bat occupancy for each directory. 

In [5]:
occupancy_dir = Path("./data/raw/bat_occupancy/")

occupancy_df = pl.concat([
    pl.read_csv(f).filter(pl.col("year") == 2019)
    .select(["species", "grts", "mean", "year", "dif"])
    .unique(["species", "grts", "year"])
    for f in occupancy_dir.glob("*.csv")
]).pivot(
    index=["grts"], on=["species"], values=["mean"]
).to_pandas()

occupancy_df.head()

grts    MYLE    LANO  MYVO  MYEV    EPFU    MYLU    MYSE  MYYU    LACI  \
0   US27967  0.0801  0.8619   NaN   NaN  0.5908  0.2925  0.1536   NaN  0.1480   
1   US64304  0.3166  0.7144   NaN   NaN  0.5833  0.8734  0.8169   NaN  0.5865   
2  US133377  0.1634  0.5693   NaN   NaN  0.5298  0.4406  0.1971   NaN  0.3395   
3  CA115980  0.0558  0.7438   NaN   NaN  0.2745  0.7074  0.3175   NaN  0.4193   
4   US78047  0.1201  0.7068   NaN   NaN  0.5227  0.5400  0.3925   NaN  0.3017   

     MYGR    PESU  MYTH  
0  0.7780  0.3284   NaN  
1     NaN  0.3943   NaN  
2  0.4474  0.1261   NaN  
3     NaN  0.0792   NaN  
4     NaN  0.1757   NaN

Now, merge the two datasets together.

In [45]:
full_df = gdf.merge(occupancy_df, left_on="grts", right_on="grts", how="left")
# remove any cells with no bats
full_df = full_df[
    ~full_df[
        [
            "MYLE",
            "LANO",
            "MYVO",
            "MYEV",
            "EPFU",
            "MYLU",
            "MYSE",
            "MYYU",
            "LACI",
            "MYGR",
            "PESU",
            "MYTH",
        ]
    ]
    .isna()
    .all(axis=1)
]

full_df

grts frame  GRTS_ID    admin1              admin2       long  \
0            US2    US        2  Colorado       Colorado_Mesa -108.77011   
1            US5    US        5   Montana     Montana_Cascade -111.58647   
2            US6    US        6    Kansas        Kansas_Rooks  -99.24916   
3            US8    US        8  Arkansas     Arkansas_Dallas  -92.60038   
4           US13    US       13     Texas  Texas_Throckmorton  -99.43737   
...          ...   ...      ...       ...                 ...        ...   
180016  CA339970    CA   339970     Yukon         Yukon_Yukon -136.51282   
180018  CA340143    CA   340143     Yukon         Yukon_Yukon -132.38769   
180020  CA340270    CA   340270     Yukon         Yukon_Yukon -127.34310   
180021  CA340277    CA   340277     Yukon         Yukon_Yukon -135.55184   
180022  CA340295    CA   340295     Yukon         Yukon_Yukon -136.16352   

             lat  karst  p_forest  p_wetland  ...    MYVO    MYEV    EPFU  \
0       39.29336      0         0          0  ...  0.1043  0.3080  0.7978   
1       47.42041      0         0          0  ...  0.4812  0.2721  0.4760   
2       39.19037      1         0          0  ...     NaN     NaN  0.6903   
3       33.91447      0        96          3  ...     NaN     NaN  0.4348   
4       33.28626      1         0          0  ...  0.0002     NaN     NaN   
...          ...    ...       ...        ...  ...     ...     ...     ...   
180016  62.29300      0        98          1  ...  0.1216  0.1286     NaN   
180018  61.23804      0        92          0  ...  0.0824  0.1363     NaN   
180020  60.72390      1        98          1  ...  0.2611  0.1197     NaN   
180021  62.24794      0        14          0  ...  0.1054  0.0516     NaN   
180022  60.30059      0        13          0  ...  0.1257  0.2677     NaN   

          MYLU    MYSE   MYYU    LACI MYGR    PESU    MYTH  
0       0.4989     NaN  0.305  0.7271  NaN     NaN  0.4778  
1       0.4573     NaN    NaN  0.4108  NaN     NaN  0.2653  
2       0.0356  0.0817    NaN  0.6007  NaN     NaN     NaN  
3          NaN  0.0493    NaN  0.1109  NaN  0.4989     NaN  
4          NaN     NaN    NaN     NaN  NaN     NaN     NaN  
...        ...     ...    ...     ...  ...     ...     ...  
180016     NaN     NaN  0.000     NaN  NaN     NaN     NaN  
180018  0.9634     NaN  0.000     NaN  NaN     NaN     NaN  
180020     NaN     NaN  0.000  0.1471  NaN     NaN     NaN  
180021     NaN     NaN  0.000     NaN  NaN     NaN     NaN  
180022  0.9268     NaN  0.000  0.2939  NaN     NaN     NaN  

[106622 rows x 35 columns]

In [46]:
michigan_subset = full_df[full_df["admin1"] == "Michigan"]
print(michigan_subset.columns)
michigan_subset

Index(['grts', 'frame', 'GRTS_ID', 'admin1', 'admin2', 'long', 'lat', 'karst',
       'p_forest', 'p_wetland', 'mean_temp', 'precip', 'DEM_max', 'physio_div',
       'dist_mines', 'riverlake', 'eco1_name', 'eco2_name', 'eco3_name',
       'eco1_num', 'eco2_num', 'eco3_num', 'geometry', 'MYLE', 'LANO', 'MYVO',
       'MYEV', 'EPFU', 'MYLU', 'MYSE', 'MYYU', 'LACI', 'MYGR', 'PESU', 'MYTH'],
      dtype='object')


grts frame  GRTS_ID    admin1                 admin2      long  \
15         US35    US       35  Michigan   Michigan_Schoolcraft -86.28162   
39         US79    US       79  Michigan       Michigan_Saginaw -83.95518   
95        US163    US      163  Michigan  Michigan_Presque Isle -83.69475   
121       US207    US      207  Michigan     Michigan_Roscommon -84.51246   
124       US211    US      211  Michigan         Michigan_Emmet -85.08868   
...         ...   ...      ...       ...                    ...       ...   
81883  US133725    US   133725  Michigan   Michigan_Montmorency -84.27956   
81886  US133733    US   133733  Michigan       Michigan_Sanilac -82.76788   
81914  US133782    US   133782  Michigan       Michigan_Saginaw -83.90813   
81925  US133797    US   133797  Michigan         Michigan_Huron -83.03566   
81931  US133804    US   133804  Michigan      Michigan_Houghton -88.62564   

            lat  karst  p_forest  p_wetland  ...  MYVO  MYEV    EPFU    MYLU  \
15     46.05096      1        10         77  ...   NaN   NaN  0.8977  0.9940   
39     43.14878      0         8          0  ...   NaN   NaN  0.3712  0.3669   
95     45.29586      1        17         27  ...   NaN   NaN  0.8109  0.8518   
121    44.28248      1        73         19  ...   NaN   NaN  0.7956  0.9065   
124    45.41641      1         6          0  ...   NaN   NaN  0.7394  0.6001   
...         ...    ...       ...        ...  ...   ...   ...     ...     ...   
81883  44.89534      0        83          2  ...   NaN   NaN  0.7282  0.7653   
81886  43.48576      0         0          0  ...   NaN   NaN  0.3825  0.3002   
81914  43.41528      0         4          0  ...   NaN   NaN  0.3992  0.3765   
81925  44.05541      0         1          2  ...   NaN   NaN  0.3823  0.3351   
81931  47.10388      0        67         13  ...   NaN   NaN  0.7290  0.9439   

         MYSE  MYYU    LACI MYGR    PESU MYTH  
15     0.5733   NaN  0.9469  NaN  0.2375  NaN  
39     0.2691   NaN  0.3210  NaN  0.0900  NaN  
95     0.2922   NaN  0.8844  NaN     NaN  NaN  
121    0.1837   NaN  0.9050  NaN  0.2122  NaN  
124    0.2236   NaN  0.8065  NaN  0.1418  NaN  
...       ...   ...     ...  ...     ...  ...  
81883  0.2548   NaN  0.8697  NaN  0.1473  NaN  
81886  0.2948   NaN  0.5202  NaN  0.0498  NaN  
81914  0.2860   NaN  0.5214  NaN  0.0618  NaN  
81925  0.2788   NaN  0.5232  NaN     NaN  NaN  
81931  0.7201   NaN  0.8607  NaN  0.1485  NaN  

[1884 rows x 35 columns]

In [48]:
m = folium.Map(zoom_start=6, location=[44.3148, -85.6024])

for _, r in michigan_subset.iterrows():
    poly_dat = gpd.GeoSeries(r["geometry"]).to_json()
    geo_j = folium.GeoJson(data=poly_dat)
    info = pd.DataFrame(
        r[["mean_temp", "precip", "dist_mines", "riverlake", "EPFU", "LANO"]]
    ).to_html()
    folium.Popup(info).add_to(geo_j)
    geo_j.add_to(m)

m

In [ ]:
m.save("example_map.html")

'<table border="1" class="dataframe">\n  <thead>\n    <tr style="text-align: right;">\n      <th></th>\n      <th>81931</th>\n    </tr>\n  </thead>\n  <tbody>\n    <tr>\n      <th>mean_temp</th>\n      <td>4.69186</td>\n    </tr>\n    <tr>\n      <th>precip</th>\n      <td>826.17528</td>\n    </tr>\n    <tr>\n      <th>dist_mines</th>\n      <td>61.69354</td>\n    </tr>\n    <tr>\n      <th>riverlake</th>\n      <td>1.0</td>\n    </tr>\n    <tr>\n      <th>EPFU</th>\n      <td>0.729</td>\n    </tr>\n    <tr>\n      <th>LANO</th>\n      <td>0.8229</td>\n    </tr>\n  </tbody>\n</table>'